In [148]:
### Prelude

import pandas as pd
#import geopandas as gpd
import numpy as np
from pathlib import Path
import seaborn as sns
import matplotlib.pyplot as plt
import glob
import os
import plotly.express as px
import json
import geojson
from urllib.request import urlopen
import plotly.offline as py
py.init_notebook_mode(connected=True)
import plotly.io as pio
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import cross_val_score, train_test_split
from sklearn.ensemble import AdaBoostRegressor
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import StandardScaler
from sklearn.impute import KNNImputer
from sklearn.pipeline import Pipeline
from sklearn.tree import DecisionTreeClassifier
from sklearn.cluster import AgglomerativeClustering
from sklearn.metrics import silhouette_score
from sklearn.manifold import TSNE
from sklearn.decomposition import PCA
pio.renderers.default='notebook'

In [2]:
nutrients   = ["energy_fat", "energy_saturate", "energy_sugar", "energy_protein","energy_carb","energy_fibre", "energy_alcohol"]
ethnicities = ["perc_ethnicity_white_2011","perc_ethnicity_mixed_2011","perc_ethnicity_asian_2011","perc_ethnicity_black_2011","perc_ethnicity_other_2011","perc_ethnicity_bame_2011"]
religions   = ["perc_religion_christian_2011","perc_religion_buddhist_2011","perc_religion_hindu_2011","perc_religion_jewish_2011","perc_religion_muslim_2011","perc_religion_sikh_2011","perc_religion_other_religion_2011","perc_religion_no_religion_2011"]
products    = ["f_beer","f_dairy","f_eggs","f_fats_oils","f_fish","f_fruit_veg","f_grains","f_meat_red","f_poultry","f_readymade","f_sauces","f_soft_drinks","f_spirits","f_sweets","f_tea_coffee","f_water","f_wine"]
education   = ["qualification_no_qualification_2011","qualification_level_1_2011","qualification_level_2_2011","qualification_apprenticeship_2011","qualification_level_3_2011","qualification_level_4_2011","qualification_other_qualifications_2011","qualification_students_2011"]
months      = ["Jan", "Feb", "Mar", "Apr", "May", "Jun", "Jul", "Aug", "Sep", "Oct", "Nov", "Dec"]

## Cleaning up the social data for ease of use

In [3]:
raw_lsoa_df = pd.read_csv("./Socio_Economic_Data/lsoa-data.csv",encoding='latin1')
raw_msoa_df = pd.read_csv("./Socio_Economic_Data/msoa-data.csv",encoding='latin1')
raw_ward_df = pd.read_csv("./Socio_Economic_Data/ward-atlas-data.csv",encoding='latin1')
raw_ward_df = raw_ward_df.drop(0)

C:\Users\49171\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3071: DtypeWarning:

Columns (174,175,176,178,189,253,254) have mixed types.Specify dtype option on import or set low_memory=False.



In [4]:
# generating the new column names
def get_cleaned_column_names(df, is_ward = False):
    
    year_strings = range(1990,2021)
    year_strings = [str(val) for val in year_strings]

    ethnic_groups = ["White","Mixed","Asian","Black","BAME", "Other"]

    ward_ethnic_groups_5 = ["White","Mixed","Asian or Asian British","Black or Black British","Other"]

    ward_ethnic_groups_18 = ["White British","White Irish","White Gypsy or Irish Traveller","Other White",
                             "Mixed White and Black Caribbean","Mixed White and Black African",
                             "Mixed White and Asian", "Other Mixed","Indian","Pakistani","Bangladeshi",
                             "Chinese","Other Asian","Black Caribbean","Black African","Other Black",
                             "Arab","Other Ethnic Group"]

    employment_types = ["Total","Employee","Self-employed","Unemployed","student"]

    qualifications = ["Level 1", "Level 2", "Level 3", "Level 4", "Apprenticeship", 
                      "No qualification","Other qualifications","students"]

    religions = ["Christian","Buddhist","Hindu","Jewish","Muslim","Sikh",
             "Other religion","No religion","Religion not stated"]

    dismiss_words = ["Population Estimates", "Density", "Health", "Transport", 
                     "Car or van", "Household Composition", "All households", "All Households", "Dwelling type", 
                     "Road Casualties","Tenure","Lone Parents", "Adults in Employment",
                     "Child Benefit","Incidence of Cancer","Life Expectancy",
                     "Low Birth Weight Births","Obesity","Central Heating","Income Deprivation",
                     "Age Structure", "Mid-year Estimate", "Land Area", "Births and deaths",
                     "Population and Age","Home repossessions","Household composition","Number of properties sold",
                     "dwellings sold during year","Dwellings and Council tax","Property Type","Size of dwellings",
                     "Property build period", "Crime", "Ambulance","Childhood Obesity Prevalence", "Air Emissions",
                     "Land Use","Car access","Travel to work by bicycle","of LSOAs in worst","Nat Insurance",
                     "Election turnout","Workplace employment","Binge Drinking","A-Level Point Scores",
                     "Average GCSE capped","Pupil Absence","Out-of-Work Families","Fires","Access to green space and nature",
                     "Indices of Deprivation","Children in Poverty","Jobseekers Allowance","Benefits claimants",
                     "Happiness and Well-being","Lone Parent Not in Employment","Adults not in Employment"]

    new_col_names = []
    old_col_names = []

    for col_name in df.columns:
        new_name = ""
        for word in dismiss_words:
            if word in col_name:
                new_name += "YEET_"       
    
        # catch percentage
        if "%" in col_name or "(rates)" in col_name or "(Percentages)" in col_name:
            new_name += "perc_"
    
        # catch ethnic groups
        if "Ethnic Group" in col_name:
            new_name += "ethnicity_"
            if "5 groups" in col_name:
                new_name += "5_groups_"
                for group in ward_ethnic_groups_5:
                    if group in col_name:
                        new_name += group.lower().replace(" ","_") + "_"
            if "18 groups" in col_name:
                new_name += "18_groups_"
                for group in ward_ethnic_groups_18:
                    if group in col_name:
                        new_name += group.lower().replace(" ","_") + "_"
            if not is_ward:    
                for group in ethnic_groups:
                    if group in col_name:
                        new_name += group.lower().replace(" ","_") + "_"
    
        # country of birth
        if "Country of Birth" in col_name:
            if "Not" in col_name:
                new_name += "not_uk_born_"
            else:
                new_name += "uk_born_"
    
        # languages
        if "Language" in col_name:
            new_name += "language_"
            if "at least one" in col_name:
                new_name += "has_+16_english_speaker_"
            else:
                new_name += "has_not_+16_english_speaker_"
    
        # religion
        if "Religion" in col_name:
            new_name += "religion_"
            for religion in religions:
                if religion in col_name:
                    new_name += religion.lower().replace(" ","_") + "_"
    
        # house prices
        if "House Prices" in col_name:
            if "Median" in col_name:
                new_name += "median_house_price_"
            elif "Sales" in col_name:
                new_name += "sales_house_price_"
        
        #income 
        if "Household Income" in col_name:
            if "Median" in col_name:
                new_name += "annual_median_income_"
            if "Mean" in col_name:
                new_name += "annual_mean_income_"
        
        # economic activity
        if "Economic Activity" in col_name:
            if is_ward:
                if "Economically active" in col_name:
                    new_name += "economically_active_"
                
                if "Employment rate" in col_name:
                    if "economically_active_" not in new_name:
                        new_name += "economically_active_"
                    new_name += "employment_rate_"
                if "In employment" in col_name:
                    if "economically_active_" not in new_name:
                        new_name += "economically_active_"
                    new_name += "in_employment_"
                if "Unemployed" in col_name:
                    if "economically_active_" not in new_name:
                        new_name += "economically_active_"
                    new_name += "unemployed_"
                    
                if "Economically Inactive" in col_name:
                    new_name += "economically_inactive_"
                    
                
                
                if "24" in col_name:
                    new_name += "16_24_"
                if "64" in col_name:
                    new_name += "16_64_"
                if "74" in col_name:
                    new_name += "16_74_"    
            else:
                if "Employment Rate" in col_name:
                    new_name += "employment_rate_"
                elif "Unemployment Rate" in col_name:
                    new_name += "unemployment_rate_"
                else:    
                    new_name += "economic_activity_"
                    if "inactive" in col_name:
                        new_name += "inactive_total_"
                    else:
                        new_name += "active_"
                        for employment in employment_types:
                            if employment in col_name:
                                new_name += employment.lower().replace("-","_") + "_"
            
        # qualifications
        if "Qualifications" in col_name:
            new_name += "qualification_"
            for qualification in qualifications:
                if qualification in col_name:
                    new_name += qualification.lower().replace(" ","_") + "_"
        
        # appending the year
        for year in year_strings:
            if year in col_name:
                new_name += year
    
        if "Lower Super Output Area" == col_name:
            new_name = "lsoa_code"
        if "Middle Super Output Area" == col_name:
            new_name = "msoa_code"
        if "Names" == col_name:
            new_name = "name"
        if "MSOA Name" == col_name:
            new_name = "name"
        if "Unnamed: 1" == col_name:
            new_name = "ward_code"
        if "Unnamed: 2" == col_name or "Unnamed: 0" == col_name:
            new_name = "YEET"
        if "Unnamed: 3" == col_name:
            new_name = "name"
        
        if "YEET" not in new_name:
            old_col_names.append(col_name)
            new_col_names.append(new_name)
    
    return old_col_names, new_col_names
            
ward_old_names, ward_new_names = get_cleaned_column_names(raw_ward_df, is_ward = True)
msoa_old_names, msoa_new_names = get_cleaned_column_names(raw_msoa_df)        
lsoa_old_names, lsoa_new_names = get_cleaned_column_names(raw_lsoa_df)        

In [5]:
ltd_raw_ward_df = raw_ward_df[ward_old_names]
ltd_raw_msoa_df = raw_msoa_df[msoa_old_names]
ltd_raw_lsoa_df = raw_lsoa_df[lsoa_old_names]

ward_name_dict = dict(zip(ward_old_names, ward_new_names))
msoa_name_dict = dict(zip(msoa_old_names, msoa_new_names))
lsoa_name_dict = dict(zip(lsoa_old_names, lsoa_new_names))

ward_df = ltd_raw_ward_df.rename(ward_name_dict,axis=1)
msoa_df = ltd_raw_msoa_df.rename(msoa_name_dict,axis=1)
lsoa_df = ltd_raw_lsoa_df.rename(lsoa_name_dict,axis=1)

In [6]:
# after verifying that they do not represent actual lsoas/msoas/wards, we drop these rows
#print(lsoa_df.iloc[4835:4837])
#print(msoa_df.iloc[983])
#print(ward_df.iloc[625:628])
lsoa_df = lsoa_df.drop([4835,4836],errors="ignore")
msoa_df = msoa_df.drop(983,errors="ignore")
ward_df = ward_df.drop([626,627,628],errors="ignore")

In [7]:
save_path = "./socio_economic/"
ward_df.to_csv(save_path + "ward_data.csv")
msoa_df.to_csv(save_path + "msoa_data.csv")
lsoa_df.to_csv(save_path + "lsoa_data.csv")

## Cleaning up the geodata into easily usable jsons

In [2]:
df_load_path = "./socio_economic/"
ward_df = pd.read_csv(df_load_path + "ward_data.csv")
msoa_df = pd.read_csv(df_load_path + "msoa_data.csv")
lsoa_df = pd.read_csv(df_load_path + "lsoa_data.csv")

In [3]:
ward_path = "../Project/UK-GeoJSON-master/json/electoral/eng/wards_by_lad/"
msoa_path = "../Geo_Data/UK-GeoJSON-master/json/statistical/eng/msoa_by_lad/"
lsoa_path = "../Geo_Data/UK-GeoJSON-master/json/statistical/eng/lsoa_by_lad/"

In [4]:
def compute_border_dict(df, path, code):
    if code == "ward_code":
        alt_code = "WD13CD"
    elif code == "msoa_code":
        alt_code = "MSOA11CD"
    elif code == "lsoa_code":
        alt_code = "LSOA11CD" 
    else:
        return "no valid code passed"
        
    ls = []
    for entry in os.listdir(path):
        if (entry.endswith(".json") and entry.startswith("E")):
            with open(path + entry) as file:
                data = json.load(file)
                ls.append(data)
    dc = {}
    dc["type"] = 'FeatureCollection'
    dc["features"] = []
    for collection in ls:
        for feature in collection["features"]:
            if (feature["properties"][alt_code] in df[code].to_list()):
                f = feature
                f["id"] = feature["properties"][alt_code]
                dc["features"].append(f)   
    
    return dc

In [5]:
ward_dict = compute_border_dict(ward_df, ward_path, "ward_code")
msoa_dict = compute_border_dict(msoa_df, msoa_path, "msoa_code")
lsoa_dict = compute_border_dict(lsoa_df, lsoa_path, "lsoa_code")

FileNotFoundError: [WinError 3] The system cannot find the path specified: '../Project/UK-GeoJSON-master/json/electoral/eng/wards_by_lad/'

In [ ]:
json_dump_path = "./geo/"
with open(json_dump_path + 'ward_geometry.json', 'w') as json_path:
    json.dump(ward_dict, json_path)
with open(json_dump_path + 'msoa_geometry.json', 'w') as json_path:
    json.dump(msoa_dict, json_path)
with open(json_dump_path + 'lsoa_geometry.json', 'w') as json_path:
    json.dump(lsoa_dict, json_path)

## Testing map-building

In [8]:
json_dump_path = "./geo/"
with open(json_dump_path + 'ward_geometry.json', 'r') as json_path:
    ward_dict = json.load(json_path)
with open(json_dump_path + 'msoa_geometry.json', 'r') as json_path:
    msoa_dict = json.load(json_path)
with open(json_dump_path + 'lsoa_geometry.json', 'r') as json_path:
    lsoa_dict = json.load(json_path)

In [9]:
ward_fig = px.choropleth_mapbox(ward_df, 
                           geojson=ward_dict, 
                           locations='ward_code', 
                           color='ethnicity_5_groups_white_2011',
                           range_color=(ward_df["ethnicity_5_groups_white_2011"].min(), 
                                        ward_df["ethnicity_5_groups_white_2011"].max()),
                           color_continuous_scale="Bluered",
                           mapbox_style="carto-positron",
                           zoom=9, center = {"lat": 51.509865, "lon": -0.118092},
                           opacity=0.5,
                           labels={'White Population Count By Ward'}
                          )
ward_fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
ward_fig.show()

KeyboardInterrupt: 

In [1]:
msoa_fig = px.choropleth_mapbox(msoa_combined_year, 
                           geojson=msoa_dict, 
                           locations='msoa_code', 
                           mapbox_style="carto-positron",
                           color='perc_ethnicity_white_2011',
                           zoom=9, center = {"lat": 51.509865, "lon": -0.118092},
                           opacity=0.35,
                           labels={'Clustering of Ethnicities on the MSOA Level'}
                          )
msoa_fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
msoa_fig.show()

html = py.plot(msoa_fig, auto_open=False, output_type='div')
with open("./../fierceeagle.github.io/_includes/ethnicity_clustering.html", 'w') as file:
    file.write(html)

NameError: name 'px' is not defined

In [25]:
lsoa_fig = px.choropleth_mapbox(msoa_df, 
                           geojson=msoa_dict, 
                           locations='msoa_code', 
                           color='perc_ethnicity_bame_2011',
                           range_color=(lsoa_df["perc_ethnicity_bame_2011"].min(), 
                                        lsoa_df["perc_ethnicity_bame_2011"].max()),
                           color_continuous_scale="Bluered",
                           mapbox_style="carto-positron",
                           zoom=9, center = {"lat": 51.509865, "lon": -0.118092},
                           opacity=0.5,
                           labels={'White Population Count By LSOA'}
                          )
lsoa_fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
lsoa_fig.show()



In [30]:
lsoa_fig = px.choropleth_mapbox(msoa_df, 
                           geojson=msoa_dict, 
                           locations='msoa_code', 
                           color='annual_median_income_2011',
                           range_color=(lsoa_df["annual_median_income_2011"].min(), 
                                        lsoa_df["annual_median_income_2011"].max()),
                           color_continuous_scale="Bluered",
                           mapbox_style="carto-positron",
                           zoom=9, center = {"lat": 51.509865, "lon": -0.118092},
                           opacity=0.5,
                           labels={'White Population Count By LSOA'}
                          )
lsoa_fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
lsoa_fig.show()

In [ ]:
html = py.plot(ward_fig, auto_open=False, output_type='div')
with open("./../fierceeagle.github.io/_includes/white_in_wards.html", 'w') as file:
    file.write(html)

In [50]:
html = py.plot(msoa_fig, auto_open=False, output_type='div')
with open("./../fierceeagle.github.io/_includes/placeholder_title.html", 'w') as file:
    file.write(html)

In [37]:
html = py.plot(lsoa_fig, auto_open=False, output_type='div')
with open("./../fierceeagle.github.io/_includes/household_income_in_lsoas.html", 'w') as file:
    file.write(html)